<a href="https://colab.research.google.com/github/open-mmlab/mmaction2/blob/master/demo/mmaction2_tutorial.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# MMAction2 Tutorial

Welcome to MMAction2! This is the official colab tutorial for using MMAction2. In this tutorial, you will learn
- Perform inference with a MMAction2 recognizer.
- Train a new recognizer with a new dataset.

Let's start!

## Install MMAction2

In [1]:
# Check nvcc version
!nvcc -V
# Check GCC version
!gcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2020 NVIDIA Corporation
Built on Mon_Oct_12_20:09:46_PDT_2020
Cuda compilation tools, release 11.1, V11.1.105
Build cuda_11.1.TC455_06.29190527_0
gcc (Ubuntu 9.3.0-17ubuntu1~20.04) 9.3.0
Copyright (C) 2019 Free Software Foundation, Inc.
This is free software; see the source for copying conditions.  There is NO
warranty; not even for MERCHANTABILITY or FITNESS FOR A PARTICULAR PURPOSE.



In [ ]:
# install dependencies: (use cu101 because colab has CUDA 10.1)
!pip install -U torch==1.5.1+cu101 torchvision==0.6.1+cu101 -f https://download.pytorch.org/whl/torch_stable.html

# install mmcv-full thus we could use CUDA operators
!pip install mmcv-full==latest+torch1.5.0+cu101 -f https://download.openmmlab.com/mmcv/dist/index.html

# Install mmaction2
!rm -rf mmaction2
!git clone https://github.com/open-mmlab/mmaction2.git
%cd mmaction2

!pip install -e .

# Install some optional requirements
!pip install -r requirements/optional.txt

Looking in links: https://download.pytorch.org/whl/torch_stable.html
Requirement already up-to-date: torch==1.5.1+cu101 in /usr/local/lib/python3.6/dist-packages (1.5.1+cu101)
Requirement already up-to-date: torchvision==0.6.1+cu101 in /usr/local/lib/python3.6/dist-packages (0.6.1+cu101)
Looking in links: https://download.openmmlab.com/mmcv/dist/index.html
  Using cached https://download.openmmlab.com/mmcv/dist/latest/torch1.5.0/cu101/mmcv_full-latest%2Btorch1.5.0%2Bcu101-cp36-cp36m-manylinux1_x86_64.whl
  Found existing installation: mmcv-full 1.2.0
    Uninstalling mmcv-full-1.2.0:
      Successfully uninstalled mmcv-full-1.2.0
Cloning into 'mmaction2'...
remote: Enumerating objects: 8, done.
remote: Counting objects: 100% (8/8), done.
remote: Compressing objects: 100% (8/8), done.
remote: Total 7596 (delta 0), reused 1 (delta 0), pack-reused 7588
Receiving objects: 100% (7596/7596), 33.53 MiB | 37.44 MiB/s, done.
Resolving deltas: 100% (5329/5329), done.
/content/mmaction2
Obtaining

In [1]:
# Check Pytorch installation
import torch, torchvision
print(torch.__version__, torch.cuda.is_available())

# Check MMAction2 installation
import mmaction


# Check MMCV installation
from mmcv.ops import get_compiling_cuda_version, get_compiler_version
print(get_compiling_cuda_version())
print(get_compiler_version())

1.9.1.post3 True
11.1
GCC 9.3


## Perform inference with a MMAction2 recognizer
MMAction2 already provides high level APIs to do inference and training.

In [ ]:
!mkdir checkpoints
!wget -c https://download.openmmlab.com/mmaction/recognition/tsn/tsn_r50_1x1x3_100e_kinetics400_rgb/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth \
      -O checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth

--2020-11-20 09:38:27--  https://download.openmmlab.com/mmaction/recognition/tsn/tsn_r50_1x1x3_100e_kinetics400_rgb/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth
Resolving download.openmmlab.com (download.openmmlab.com)... 47.252.96.35
Connecting to download.openmmlab.com (download.openmmlab.com)|47.252.96.35|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 97579339 (93M) [application/octet-stream]
Saving to: ‘checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth’

checkpoints/tsn_r50 100%[===================>]  93.06M  8.48MB/s    in 11s     

2020-11-20 09:38:40 (8.49 MB/s) - ‘checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth’ saved [97579339/97579339]



In [3]:
from mmaction.apis import init_recognizer, inference_recognizer

# Choose to use a config and initialize the recognizer
config = '../configs/recognition/tsn/tsn_r50_video_inference_1x1x3_100e_kinetics400_rgb.py'
# Setup a checkpoint file to load
checkpoint = '../checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth'
# Initialize the recognizer
model = init_recognizer(config, checkpoint, device='cuda:0')

load checkpoint from local path: ../checkpoints/tsn_r50_1x1x3_100e_kinetics400_rgb_20200614-e508be42.pth


In [4]:
# Use the recognizer to do inference
video = 'demo.mp4'
label = 'label_map_k400.txt'
results = inference_recognizer(model, video, label)

In [5]:
# Let's show the results
for result in results:
    print(f'{result[0]}: ', result[1])

arm wrestling:  29.62016
rock scissors paper:  10.755016
shaking hands:  9.909008
clapping:  9.190468
massaging feet:  8.304269


## Train a recognizer on customized dataset

To train a new recognizer, there are usually three things to do:
1. Support a new dataset
2. Modify the config
3. Train a new recognizer

### Support a new dataset

In this tutorial, we gives an example to convert the data into the format of existing datasets. Other methods and more advanced usages can be found in the [doc](/docs/tutorials/new_dataset.md)

Firstly, let's download a tiny dataset obtained from [Kinetics-400](https://deepmind.com/research/open-source/open-source-datasets/kinetics/). We select 30 videos with their labels as train dataset and 10 videos with their labels as test dataset.

In [12]:
# download, decompress the data
!rm kinetics400_tiny.zip*
!rm -rf kinetics400_tiny
!wget https://download.openmmlab.com/mmaction/kinetics400_tiny.zip
!unzip kinetics400_tiny.zip > /dev/null

rm: cannot remove 'kinetics400_tiny.zip*': No such file or directory
--2021-12-11 19:54:25--  https://download.openmmlab.com/mmaction/kinetics400_tiny.zip
Resolving download.openmmlab.com (download.openmmlab.com)... 47.88.36.59
Connecting to download.openmmlab.com (download.openmmlab.com)|47.88.36.59|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 18308682 (17M) [application/zip]
Saving to: ‘kinetics400_tiny.zip’

kinetics400_tiny.zi 100%[===================>]  17.46M  10.1MB/s    in 1.7s    

2021-12-11 19:54:27 (10.1 MB/s) - ‘kinetics400_tiny.zip’ saved [18308682/18308682]



In [ ]:
# Check the directory structure of the tiny data

# Install tree first
!apt-get -q install tree
!tree kinetics400_tiny

Reading package lists...
Building dependency tree...
Reading state information...
tree is already the newest version (1.7.0-5).
0 upgraded, 0 newly installed, 0 to remove and 14 not upgraded.
kinetics400_tiny
├── kinetics_tiny_train_video.txt
├── kinetics_tiny_val_video.txt
├── train
│   ├── 27_CSXByd3s.mp4
│   ├── 34XczvTaRiI.mp4
│   ├── A-wiliK50Zw.mp4
│   ├── D32_1gwq35E.mp4
│   ├── D92m0HsHjcQ.mp4
│   ├── DbX8mPslRXg.mp4
│   ├── FMlSTTpN3VY.mp4
│   ├── h10B9SVE-nk.mp4
│   ├── h2YqqUhnR34.mp4
│   ├── iRuyZSKhHRg.mp4
│   ├── IyfILH9lBRo.mp4
│   ├── kFC3KY2bOP8.mp4
│   ├── LvcFDgCAXQs.mp4
│   ├── O46YA8tI530.mp4
│   ├── oMrZaozOvdQ.mp4
│   ├── oXy-e_P_cAI.mp4
│   ├── P5M-hAts7MQ.mp4
│   ├── phDqGd0NKoo.mp4
│   ├── PnOe3GZRVX8.mp4
│   ├── R8HXQkdgKWA.mp4
│   ├── RqnKtCEoEcA.mp4
│   ├── soEcZZsBmDs.mp4
│   ├── TkkZPZHbAKA.mp4
│   ├── T_TMNGzVrDk.mp4
│   ├── WaS0qwP46Us.mp4
│   ├── Wh_YPQdH1Zg.mp4
│   ├── WWP5HZJsg-o.mp4
│   ├── xGY2dP0YUjA.mp4
│   ├── yLC9CtWU5ws.mp4
│   └── ZQV4U2KQ370

In [7]:
# After downloading the data, we need to check the annotation format
!cat kinetics400_tiny/kinetics_tiny_train_video.txt

D32_1gwq35E.mp4 0
iRuyZSKhHRg.mp4 1
oXy-e_P_cAI.mp4 0
34XczvTaRiI.mp4 1
h2YqqUhnR34.mp4 0
O46YA8tI530.mp4 0
kFC3KY2bOP8.mp4 1
WWP5HZJsg-o.mp4 1
phDqGd0NKoo.mp4 1
yLC9CtWU5ws.mp4 0
27_CSXByd3s.mp4 1
IyfILH9lBRo.mp4 1
T_TMNGzVrDk.mp4 1
TkkZPZHbAKA.mp4 0
PnOe3GZRVX8.mp4 1
soEcZZsBmDs.mp4 1
FMlSTTpN3VY.mp4 1
WaS0qwP46Us.mp4 0
A-wiliK50Zw.mp4 1
oMrZaozOvdQ.mp4 1
ZQV4U2KQ370.mp4 0
DbX8mPslRXg.mp4 1
h10B9SVE-nk.mp4 1
P5M-hAts7MQ.mp4 0
R8HXQkdgKWA.mp4 0
D92m0HsHjcQ.mp4 0
RqnKtCEoEcA.mp4 0
LvcFDgCAXQs.mp4 0
xGY2dP0YUjA.mp4 0
Wh_YPQdH1Zg.mp4 0


In [1]:
!cat ../data/survai_var_mk1/survai_var_mk1_train_list.txt

ru/19QCaRYQOXU14_000216_000224.mp4 9
cr/vHbyxKQxnBs4_000037_000041.mp4 5
st/VuMRM2QonKc31_000559_000565.mp4 10
cr/m_dbBk3k1Vw21_000177_000197.mp4 5
ar/ZkAE0mIcqFk1_000089_000119.mp4 2
pg/ebolOvmrW907_000035_000039.mp4 6
st/oxKY96LISk45_000080_000082.mp4 10
ru/YY-virWnjoA2_000003_000008.mp4 9
st/oxKY96LISk44_000076_000078.mp4 10
cr/-sPYqifV7U06_000029_000033.mp4 5
cr/IZvA7elG3lg8_000060_000063.mp4 5
st/wL-tPhqz_5I24_000158_000160.mp4 10
ru/c8j3h7fuYsY7_000081_000084.mp4 9
st/Mq6h_EzhsYM23_000207_000215.mp4 10
po/2IWeIq52meQ2_000006_000009.mp4 7
br/kbNUQIA-1o02_000056_000061.mp4 4
st/cq7uPGkI9Lo3_000007_000009.mp4 10
ar/sMOieZKAB3k6_000018_000036.mp4 2
pg/eppIM1LWppM17_000204_000219.mp4 6
st/UHa-PLwBgkI8_000054_000056.mp4 10
st/m_dbBk3k1Vw18_000143_000145.mp4 10
cr/x3e9-wrSDR416_000222_000234.mp4 5
ad/DW5Lanit0X816_000137_000140.mp4 0
ru/9KpB7KeJdV011_000171_000173.mp4 9
st/VuMRM2QonKc4_000098_000100.mp4 10
cr/qnpMkLKsLCA1_000002_000004.mp4 5
cr/YKjnSPK0ub04_000087_000091.mp4 5
cr/W4fwia

According to the format defined in [`VideoDataset`](./datasets/video_dataset.py), each line indicates a sample video with the filepath and label, which are split with a whitespace.

### Modify the config

In the next step, we need to modify the config for the training.
To accelerate the process, we finetune a recognizer using a pre-trained recognizer.

In [1]:
from mmcv import Config
cfg = Config.fromfile('../configs/recognition/swin/swin_base_patch244_window877_kinetics400_22k.py')

Given a config that trains a TSN model on kinetics400-full dataset, we need to modify some values to use it for training TSN on Kinetics400-tiny dataset.


In [2]:
from mmcv.runner import set_random_seed

# Modify dataset type and path
cfg.dataset_type = 'VideoDataset'
cfg.data_root = '../data/survai_var_mk1/videos_train'
cfg.data_root_val = '../data/survai_var_mk1/videos_val'
cfg.ann_file_train = '../data/survai_var_mk1/survai_var_mk1_train_list.txt'
cfg.ann_file_val = '../data/survai_var_mk1/survai_var_mk1_val_list.txt'
cfg.ann_file_test = '../data/survai_var_mk1/survai_var_mk1_val_list.txt'


cfg.data.test.type = 'VideoDataset'
cfg.data.test.ann_file = '../data/survai_var_mk1/survai_var_mk1_val_list.txt'
cfg.data.test.data_prefix = '../data/survai_var_mk1/videos_val'

cfg.data.train.type = 'VideoDataset'
cfg.data.train.ann_file = '../data/survai_var_mk1/survai_var_mk1_train_list.txt'
cfg.data.train.data_prefix = '../data/survai_var_mk1/videos_train'

cfg.data.val.type = 'VideoDataset'
cfg.data.val.ann_file = '../data/survai_var_mk1/survai_var_mk1_val_list.txt'
cfg.data.val.data_prefix = '../data/survai_var_mk1/videos_val'

# The flag is used to determine whether it is omnisource training
cfg.setdefault('omnisource', False)
# Modify num classes of the model in cls_head
cfg.model.cls_head.num_classes = 10
# We can use the pre-trained TSN model
cfg.load_from = '../precheckpoints/swin_base_patch244_window877_kinetics400_22k.pth'
#cfg.resume_from = '../logs/mark1_5vcontinuedafter20/epoch_21.pth'
# Set up working dir to save files and logs.
cfg.work_dir = '../logs/mark1_9_10c_lr8'

# The original learning rate (LR) is set for 8-GPU training.
# We divide it by 8 since we only use one GPU.
cfg.data.videos_per_gpu = 20
cfg.data.workers_per_gpu = 8
cfg.optimizer.lr = cfg.optimizer.lr / 8 #/ 16
cfg.total_epochs = 70

# We can set the checkpoint saving interval to reduce the storage cost
cfg.checkpoint_config.interval = 3
# We can set the log print interval to reduce the the times of printing log
cfg.log_config.interval = 5

# Set seed thus the results are more reproducible
cfg.seed = 0
set_random_seed(0, deterministic=False)
cfg.gpu_ids = range(1)


# We can initialize the logger for training and have a look
# at the final config used for training
print(f'Config:\n{cfg.pretty_text}')


Config:
model = dict(
    type='Recognizer3D',
    backbone=dict(
        type='SwinTransformer3D',
        patch_size=(2, 4, 4),
        embed_dim=128,
        depths=[2, 2, 18, 2],
        num_heads=[4, 8, 16, 32],
        window_size=(8, 7, 7),
        mlp_ratio=4.0,
        qkv_bias=True,
        qk_scale=None,
        drop_rate=0.0,
        attn_drop_rate=0.0,
        drop_path_rate=0.2,
        patch_norm=True),
    cls_head=dict(
        type='I3DHead',
        in_channels=1024,
        num_classes=10,
        spatial_type='avg',
        dropout_ratio=0.5),
    test_cfg=dict(average_clips=None, max_testing_views=2))
checkpoint_config = dict(interval=3)
log_config = dict(interval=5, hooks=[dict(type='TextLoggerHook')])
dist_params = dict(backend='nccl')
log_level = 'INFO'
load_from = '../precheckpoints/swin_base_patch244_window877_kinetics400_22k.pth'
resume_from = None
workflow = [('train', 1)]
dataset_type = 'VideoDataset'
data_root = '../data/survai_var_mk1/videos_train'
data_

### Train a new recognizer

Finally, lets initialize the dataset and recognizer, then train a new recognizer!

In [3]:
import os.path as osp

from mmaction.datasets import build_dataset
from mmaction.models import build_model
from mmaction.apis import train_model

import mmcv

# Build the dataset
datasets = [build_dataset(cfg.data.train)]

# Build the recognizer
model = build_model(cfg.model, train_cfg=cfg.get('train_cfg'), test_cfg=cfg.get('test_cfg'))

# Create work_dir
mmcv.mkdir_or_exist(osp.abspath(cfg.work_dir))
train_model(model, datasets, cfg, distributed=False, validate=True)

2022-01-28 06:27:59,061 - mmaction - INFO - load checkpoint from local path: ../precheckpoints/swin_base_patch244_window877_kinetics400_22k.pth
2022-01-28 06:27:59,213 - mmaction - WARNING - The model and loaded state dict do not match exactly

size mismatch for cls_head.fc_cls.weight: copying a param with shape torch.Size([400, 1024]) from checkpoint, the shape in current model is torch.Size([10, 1024]).
size mismatch for cls_head.fc_cls.bias: copying a param with shape torch.Size([400]) from checkpoint, the shape in current model is torch.Size([10]).
2022-01-28 06:27:59,222 - mmaction - INFO - Start running, host: beanbagthomas@elita-MS-7B98, work_dir: /home/beanbagthomas/code/hrf/Video-Swin-Transformer/logs/mark1_9_10c_lr8
2022-01-28 06:27:59,223 - mmaction - INFO - Hooks will be executed in the following order:
before_run:
(VERY_HIGH   ) CosineAnnealingLrUpdaterHook       
(ABOVE_NORMAL) DistOptimizerHook                  
(NORMAL      ) CheckpointHook                     
(NORMAL 

Selected optimization level O1:  Insert automatic casts around Pytorch functions and Tensor methods.

Defaults for this optimization level are:
enabled                : True
opt_level              : O1
cast_model_type        : None
patch_torch_functions  : True
keep_batchnorm_fp32    : None
master_weights         : None
loss_scale             : dynamic
Processing user overrides (additional kwargs that are not None)...
After processing overrides, optimization options are:
enabled                : True
opt_level              : O1
cast_model_type        : None
patch_torch_functions  : True
keep_batchnorm_fp32    : None
master_weights         : None
loss_scale             : dynamic


/home/beanbagthomas/code/hrf/Swin-Transformer-Object-Detection/mmcv/mmcv/runner/hooks/evaluation.py:222: UserWarning: runner.meta is None. Creating an empty one.
  warnings.warn('runner.meta is None. Creating an empty one.')
2022-01-28 06:28:07,231 - mmaction - INFO - Epoch [1][5/1699]	lr: 3.782e-07, eta: 2 days, 4:52:50, time: 1.601, data_time: 0.731, memory: 17235, top1_acc: 0.1000, top5_acc: 0.5000, loss_cls: 2.4167, loss: 2.4167
2022-01-28 06:28:09,121 - mmaction - INFO - Epoch [1][10/1699]	lr: 3.822e-07, eta: 1 day, 8:40:54, time: 0.378, data_time: 0.001, memory: 17916, top1_acc: 0.0000, top5_acc: 0.0000, loss_cls: 2.6161, loss: 2.6161
2022-01-28 06:28:10,967 - mmaction - INFO - Epoch [1][15/1699]	lr: 3.861e-07, eta: 1 day, 1:51:12, time: 0.369, data_time: 0.001, memory: 17923, top1_acc: 0.1000, top5_acc: 0.3000, loss_cls: 2.4995, loss: 2.4995
2022-01-28 06:28:12,847 - mmaction - INFO - Epoch [1][20/1699]	lr: 3.901e-07, eta: 22:29:35, time: 0.376, data_time: 0.001, memory: 17926, 

Gradient overflow.  Skipping step, loss scaler 0 reducing loss scale to 32768.0


2022-01-28 06:29:44,476 - mmaction - INFO - Epoch [1][260/1699]	lr: 5.808e-07, eta: 13:20:37, time: 0.416, data_time: 0.001, memory: 17931, top1_acc: 0.0000, top5_acc: 0.3000, loss_cls: 2.4155, loss: 2.4155
2022-01-28 06:29:46,536 - mmaction - INFO - Epoch [1][265/1699]	lr: 5.848e-07, eta: 13:20:51, time: 0.412, data_time: 0.001, memory: 17931, top1_acc: 0.2000, top5_acc: 0.6000, loss_cls: 2.1947, loss: 2.1947
2022-01-28 06:29:48,578 - mmaction - INFO - Epoch [1][270/1699]	lr: 5.887e-07, eta: 13:20:56, time: 0.408, data_time: 0.001, memory: 17931, top1_acc: 0.2000, top5_acc: 0.5000, loss_cls: 2.3419, loss: 2.3419
2022-01-28 06:29:50,665 - mmaction - INFO - Epoch [1][275/1699]	lr: 5.927e-07, eta: 13:21:21, time: 0.417, data_time: 0.001, memory: 17931, top1_acc: 0.3000, top5_acc: 0.8000, loss_cls: 2.1681, loss: 2.1681
2022-01-28 06:29:52,742 - mmaction - INFO - Epoch [1][280/1699]	lr: 5.967e-07, eta: 13:21:40, time: 0.415, data_time: 0.001, memory: 17931, top1_acc: 0.0000, top5_acc: 0.50

...

2022-01-28 19:54:35,463 - mmaction - INFO - Epoch [69][425/1699]	lr: 7.548e-09, eta: 0:19:04, time: 0.392, data_time: 0.000, memory: 17936, top1_acc: 0.8000, top5_acc: 1.0000, loss_cls: 0.5623, loss: 0.5623
2022-01-28 19:54:37,448 - mmaction - INFO - Epoch [69][430/1699]	lr: 7.548e-09, eta: 0:19:02, time: 0.397, data_time: 0.001, memory: 17936, top1_acc: 0.6000, top5_acc: 0.9000, loss_cls: 1.3308, loss: 1.3308
2022-01-28 19:54:39,410 - mmaction - INFO - Epoch [69][435/1699]	lr: 7.548e-09, eta: 0:19:00, time: 0.392, data_time: 0.000, memory: 17936, top1_acc: 0.7000, top5_acc: 1.0000, loss_cls: 0.8998, loss: 0.8998
2022-01-28 19:54:41,381 - mmaction - INFO - Epoch [69][440/1699]	lr: 7.548e-09, eta: 0:18:58, time: 0.394, data_time: 0.000, memory: 17936, top1_acc: 0.7000, top5_acc: 1.0000, loss_cls: 0.5604, loss: 0.5604
2022-01-28 19:54:43,371 - mmaction - INFO - Epoch [69][445/1699]	lr: 7.548e-09, eta: 0:18:56, time: 0.398, data_time: 0.000, memory: 17936, top1_acc: 0.8000, top5_acc: 1.00

Gradient overflow.  Skipping step, loss scaler 0 reducing loss scale to 1024.0


2022-01-28 19:57:45,022 - mmaction - INFO - Epoch [69][920/1699]	lr: 7.548e-09, eta: 0:15:53, time: 0.390, data_time: 0.000, memory: 17936, top1_acc: 0.9000, top5_acc: 1.0000, loss_cls: 0.8313, loss: 0.8313
2022-01-28 19:57:47,010 - mmaction - INFO - Epoch [69][925/1699]	lr: 7.548e-09, eta: 0:15:51, time: 0.398, data_time: 0.000, memory: 17936, top1_acc: 0.7000, top5_acc: 0.9000, loss_cls: 1.0724, loss: 1.0724
2022-01-28 19:57:48,961 - mmaction - INFO - Epoch [69][930/1699]	lr: 7.548e-09, eta: 0:15:50, time: 0.390, data_time: 0.000, memory: 17936, top1_acc: 0.7000, top5_acc: 1.0000, loss_cls: 0.7345, loss: 0.7345
2022-01-28 19:57:50,934 - mmaction - INFO - Epoch [69][935/1699]	lr: 7.548e-09, eta: 0:15:48, time: 0.395, data_time: 0.000, memory: 17936, top1_acc: 0.8000, top5_acc: 1.0000, loss_cls: 0.5835, loss: 0.5835
2022-01-28 19:57:52,919 - mmaction - INFO - Epoch [69][940/1699]	lr: 7.548e-09, eta: 0:15:46, time: 0.397, data_time: 0.001, memory: 17936, top1_acc: 0.6000, top5_acc: 1.00

[>>>>>>>>>>>>>>>>>>>>>>>>>>>] 1097/1097, 4.1 task/s, elapsed: 270s, ETA:     0s

2022-01-28 20:17:59,823 - mmaction - INFO - Evaluating top_k_accuracy ...
2022-01-28 20:17:59,825 - mmaction - INFO - 
top1_acc	0.5907
top5_acc	0.9608
2022-01-28 20:17:59,825 - mmaction - INFO - Evaluating mean_class_accuracy ...
2022-01-28 20:17:59,826 - mmaction - INFO - 
mean_acc	0.5544
2022-01-28 20:17:59,827 - mmaction - INFO - Epoch(val) [70][1097]	top1_acc: 0.5907, top5_acc: 0.9608, mean_class_accuracy: 0.5544


### Understand the log
From the log, we can have a basic understanding the training process and know how well the recognizer is trained.

Firstly, the ResNet-50 backbone pre-trained on ImageNet is loaded, this is a common practice since training from scratch is more cost. The log shows that all the weights of the ResNet-50 backbone are loaded except the `fc.bias` and `fc.weight`.

Second, since the dataset we are using is small, we loaded a TSN model and finetune it for action recognition.
The original TSN is trained on original Kinetics-400 dataset which contains 400 classes but Kinetics-400 Tiny dataset only have 2 classes. Therefore, the last FC layer of the pre-trained TSN for classification has different weight shape and is not used.

Third, after training, the recognizer is evaluated by the default evaluation. The results show that the recognizer achieves 100% top1 accuracy and 100% top5 accuracy on the val dataset,
 
Not bad!

## Test the trained recognizer

After finetuning the recognizer, let's check the prediction results!

In [22]:
from mmaction.apis import single_gpu_test
from mmaction.datasets import build_dataloader
from mmcv.parallel import MMDataParallel
from mmaction.datasets import build_dataset
from mmaction.models import build_model
from mmcv import Config

#cfg = Config.fromfile('../configs/recognition/swin/swin_base_patch244_window877_kinetics400_22k_custom.py')
#cfg.load_from = '../logs/mark1_1_exp/epoch_30.pth'

# Build a test dataloader
dataset = build_dataset(cfg.data.test, dict(test_mode=True))
data_loader = build_dataloader(
        dataset,
        videos_per_gpu=1,
        workers_per_gpu=cfg.data.workers_per_gpu,
        dist=False,
        shuffle=False)
        
#model = build_model(cfg.model, train_cfg=cfg.get('train_cfg'), test_cfg=cfg.get('test_cfg'))
model = MMDataParallel(model, device_ids=[0])
outputs = single_gpu_test(model, data_loader)

eval_config = cfg.evaluation
eval_config.pop('interval')
eval_res = dataset.evaluate(outputs, **eval_config)
for name, val in eval_res.items():
    print(f'{name}: {val:.04f}')

[>>>>>>>>>>>>>>>>>>>>>>>>>>>>>] 564/564, 1.1 task/s, elapsed: 500s, ETA:     0s
Evaluating top_k_accuracy ...

top1_acc	0.5337
top5_acc	0.9504

Evaluating mean_class_accuracy ...

mean_acc	0.4578
top1_acc: 0.5337
top5_acc: 0.9504
mean_class_accuracy: 0.4578
